In [0]:
storage_account_name = "sushilstore"
storage_account_key = "BBKRRBiRdx6/0OV+UOSa6nisx4GlnqwwohTVf2YCBBnYKl2Mhbhxi9AnK/hw/ug895yFa2ASSvgs+ASt17JM7Q=="

mount_points = {
    "bronze-layer": "/mnt/retail/bronze-layer",

}

containers = {
    "bronze-layer": "bronze-layer",
}

def mount_container(container_name, mount_point):
    if not any(mount.mountPoint == mount_point for mount in dbutils.fs.mounts()):
        dbutils.fs.mount(
            source=f"wasbs://{container_name}@{storage_account_name}.blob.core.windows.net",
            mount_point=mount_point,
            extra_configs={f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_key}
        )
        print(f"Mounted {container_name} at {mount_point}")
    else:
        print(f"{mount_point} is already mounted.")

for container, mount_point in mount_points.items():
    mount_container(containers[container], mount_point)

dbutils.fs.mounts()


/mnt/retail/bronze-layer is already mounted.


[MountInfo(mountPoint='/databricks-datasets', source='databricks-datasets', encryptionType=''),
 MountInfo(mountPoint='/mnt/retail/gold-layer', source='wasbs://gold-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/Volumes', source='UnityCatalogVolumes', encryptionType=''),
 MountInfo(mountPoint='/mnt/online-retail/silver-layer', source='wasbs://silver-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/databricks/mlflow-tracking', source='databricks/mlflow-tracking', encryptionType=''),
 MountInfo(mountPoint='/databricks-results', source='databricks-results', encryptionType=''),
 MountInfo(mountPoint='/databricks/mlflow-registry', source='databricks/mlflow-registry', encryptionType=''),
 MountInfo(mountPoint='/mnt/retail/bronze-layer', source='wasbs://bronze-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/Volume', source='DbfsReserved', encryptionType=''),
 MountI

In [0]:
%fs ls dbfs:/mnt/retail/bronze-layer/

path name size modificationTime dbfs:/mnt/retail/bronze-layer/Online Retail.parquet Online Retail.parquet 12344740 1734420498000

In [0]:


Online_Retail_file_path = "dbfs:/mnt/retail/bronze-layer/Online Retail.parquet"

Online_Retail_df = spark.read.parquet(Online_Retail_file_path, header=True, inferSchema=True)

print("Online Retail Data:")
Online_Retail_df.show(5)



Online Retail Data:
+---------+---------+--------------------+--------+----------------+---------+----------+--------------+
|InvoiceNo|StockCode|         Description|Quantity|     InvoiceDate|UnitPrice|CustomerID|       Country|
+---------+---------+--------------------+--------+----------------+---------+----------+--------------+
|   536365|   85123A|WHITE HANGING HEA...|       6|01-12-2010 08:26|     2.55|     17850|United Kingdom|
|   536365|    71053| WHITE METAL LANTERN|       6|01-12-2010 08:26|     3.39|     17850|United Kingdom|
|   536365|   84406B|CREAM CUPID HEART...|       8|01-12-2010 08:26|     2.75|     17850|United Kingdom|
|   536365|   84029G|KNITTED UNION FLA...|       6|01-12-2010 08:26|     3.39|     17850|United Kingdom|
|   536365|   84029E|RED WOOLLY HOTTIE...|       6|01-12-2010 08:26|     3.39|     17850|United Kingdom|
+---------+---------+--------------------+--------+----------------+---------+----------+--------------+
only showing top 5 rows



In [0]:
Online_Retail_df.printSchema()

root
 |-- InvoiceNo: string (nullable = true)
 |-- StockCode: string (nullable = true)
 |-- Description: string (nullable = true)
 |-- Quantity: string (nullable = true)
 |-- InvoiceDate: string (nullable = true)
 |-- UnitPrice: string (nullable = true)
 |-- CustomerID: string (nullable = true)
 |-- Country: string (nullable = true)



In [0]:
from pyspark.sql.functions import col, sum

print("Null Counts in Online Retail Data:")
null_counts = Online_Retail_df.select([sum(col(c).isNull().cast("int")).alias(c) for c in Online_Retail_df.columns])
null_counts.display()

Online_Retail_df_cleaned = (
    Online_Retail_df
    .na.fill({"Quantity": 0, "UnitPrice": 0.0, "Description": "No Description"})
    .na.drop(subset=["InvoiceNo", "StockCode", "CustomerID", "InvoiceDate", "Country"])
)



Null Counts in Online Retail Data:


InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 0 0 1454 0 0 0 135080 0

In [0]:
def check_nulls(df, name):
    print(f"Checking nulls in {name}:")
    null_counts = df.select([sum(col(c).isNull().cast("int")).alias(c) for c in df.columns])
    null_counts.display()

check_nulls(Online_Retail_df_cleaned, "Online_Retail_df_cleaned")

Checking nulls in Online_Retail_df_cleaned:


InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 0 0 0 0 0 0 0 0

In [0]:
from pyspark.sql.functions import col
dataframes = [Online_Retail_df_cleaned]  
for df in dataframes:
    columns = df.columns  
    for column in columns:
        if dict(df.dtypes)[column] in ['int', 'double', 'float']:  
            negative_values = df.filter(col(column) < 0).count()  
            if negative_values > 0:
                print(f"'{column}'  Negative.")
            else:
                print(f"'{column}'  All Positive.")

In [0]:
from pyspark.sql.functions import when

Online_Retail_df_cleaned = Online_Retail_df_cleaned.withColumn(
    "Quantity",
    when(col("Quantity") < 0, 0).otherwise(col("Quantity"))
)

dataframes = [Online_Retail_df_cleaned]
for df in dataframes:
    columns = df.columns
    for column in columns:
        if dict(df.dtypes)[column] in ['int', 'double', 'float']:
            negative_values = df.filter(col(column) < 0).count()
            if negative_values > 0:
                print(f"'{column}'  Negative.")
            else:
                print(f"'{column}'  All Positive.")


In [0]:
Online_Retail_df_cleaned = Online_Retail_df_cleaned.dropDuplicates()

print("Row counts after removing duplicates:")
print(f"Online Retail: {Online_Retail_df_cleaned.count()}")


Row counts after removing duplicates:
Online Retail: 401574


In [0]:
from pyspark.sql.functions import to_timestamp, date_format

Online_Retail_df_cleaned = Online_Retail_df_cleaned.withColumn(
    "InvoiceDate", 
    to_timestamp("InvoiceDate", "dd-MM-yyyy HH:mm")
)

Online_Retail_df_cleaned = Online_Retail_df_cleaned.withColumn(
    "InvoiceDate", 
    date_format("InvoiceDate", "yyyy-MM-dd") 
)

Online_Retail_df_cleaned.display(5)


InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536367 48187 DOORMAT NEW ENGLAND 4 2010-12-01 7.95 13047 United Kingdom 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 2010-12-01 0.85 12583 France 536446 21651 HANGING GLASS ETCHED TEALIGHT 6 2010-12-01 1.65 15983 United Kingdom 536464 85099B JUMBO BAG RED RETROSPOT 1 2010-12-01 1.95 17968 United Kingdom 536527 22809 SET OF 6 T-LIGHTS SANTA 6 2010-12-01 2.95 12662 Germany 536532 22716 CARD CIRCUS PARADE 12 2010-12-01 0.42 12433 Norway 536535 20685 DOORMAT RED RETROSPOT 2 2010-12-01 7.95 15605 United Kingdom 536562 22313 OFFICE MUG WARMER PINK 6 2010-12-01 2.95 13468 United Kingdom 536637 85135B BLUE DRAGONFLY HELICOPTER 1 2010-12-02 7.95 18041 United Kingdom 536744 22898 CHILDRENS APRON APPLES DESIGN 25 2010-12-02 1.95 14466 United Kingdom 536749 21415 CLAM SHELL SMALL 2 2010-12-02 2.1 17976 United Kingdom 536750 22752 SET 7 BABUSHKA NESTING BOXES 4 2010-12-02 7.65 17850 United Kingdom 536778 21257 VICTORIAN SEWING BOX MEDIUM 2 2010-12-02 7.95 13138 United Kingdom 536796 21357 TOAST ITS - DINOSAUR 1 2010-12-02 1.25 15574 United Kingdom 536837 22633 HAND WARMER UNION JACK 4 2010-12-02 2.1 14395 United Kingdom 536846 22443 GROW YOUR OWN HERBS SET OF 3 1 2010-12-02 7.95 14573 United Kingdom C536850 22186 RED STAR CARD HOLDER 0 2010-12-03 2.55 14213 United Kingdom 536945 22551 PLASTERS IN TIN SPACEBOY 1 2010-12-03 1.65 14083 United Kingdom 536975 22112 CHOCOLATE HOT WATER BOTTLE 9 2010-12-03 4.95 14911 EIRE 536984 82616C MIDNIGHT GLAMOUR SCARF KNITTING KIT 1 2010-12-03 2.95 17841 United Kingdom 536984 21784 SHOE SHINE BOX 1 2010-12-03 9.95 17841 United Kingdom 537023 22804 CANDLEHOLDER PINK HANGING HEART 1 2010-12-03 2.95 16725 United Kingdom 537046 85123A WHITE HANGING HEART T-LIGHT HOLDER 1 2010-12-05 2.95 18109 United Kingdom 537081 22306 SILVER MUG BONE CHINA TREE OF LIFE 36 2010-12-05 1.65 15332 Lithuania 537135 22581 WOOD STOCKING CHRISTMAS SCANDISPOT 2 2010-12-05 0.85 17059 United Kingdom 537138 22909 SET OF 20 VINTAGE CHRISTMAS NAPKINS 8 2010-12-05 0.85 17211 United Kingdom 537142 82578 KITCHEN METAL SIGN 1 2010-12-05 0.55 12748 United Kingdom 537154 22866 HAND WARMER SCOTTY DOG DESIGN 5 2010-12-05 2.1 15808 United Kingdom 537179 84879 ASSORTED COLOUR BIRD ORNAMENT 32 2010-12-05 1.69 13767 United Kingdom 537192 85187 S/12 MINI RABBIT EASTER 1 2010-12-05 1.65 16402 United Kingdom 537201 22962 JAM JAR WITH PINK LID 24 2010-12-05 0.85 12472 Germany 537201 22141 CHRISTMAS CRAFT TREE TOP ANGEL 12 2010-12-05 2.1 12472 Germany 537209 21056 DOCTOR'S BAG SOFT TOY 1 2010-12-05 8.95 14606 United Kingdom 537216 22196 SMALL HEART MEASURING SPOONS 12 2010-12-05 0.85 15502 United Kingdom 537223 22112 CHOCOLATE HOT WATER BOTTLE 6 2010-12-05 4.95 13579 United Kingdom 537224 22294 HEART FILIGREE DOVE SMALL 7 2010-12-05 1.25 13174 United Kingdom 537256 22041 RECORD FRAME 7" SINGLE SIZE " 48 2010-12-06 2.1 16210 United Kingdom 537262 15056N EDWARDIAN PARASOL NATURAL 3 2010-12-06 5.95 15039 United Kingdom 537362 22551 PLASTERS IN TIN SPACEBOY 1 2010-12-06 1.65 17596 United Kingdom 537369 22482 BLUE TEA TOWEL CLASSIC DESIGN 3 2010-12-06 1.25 17860 United Kingdom 537371 21891 TRADITIONAL WOODEN SKIPPING ROPE 2 2010-12-06 1.25 15028 United Kingdom 537385 22697 GREEN REGENCY TEACUP AND SAUCER 6 2010-12-06 2.95 14487 United Kingdom 537396 21351 CINAMMON & ORANGE WREATH 3 2010-12-06 6.75 17223 United Kingdom 537405 21361 LOVE LARGE WOOD LETTERS 1 2010-12-06 12.75 17841 United Kingdom 537422 21078 SET/20 STRAWBERRY PAPER NAPKINS 1 2010-12-06 0.85 17812 United Kingdom 537441 21181 PLEASE ONE PERSON METAL SIGN 12 2010-12-06 2.1 13564 United Kingdom 537618 17038 PORCELAIN BUDAH INCENSE HOLDER 100 2010-12-07 0.07 15061 United Kingdom 537653 20982 12 PENCILS TALL TUBE SKULLS 2 2010-12-07 0.85 17897 United Kingdom 536375 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 2010-12-01 4.25 17850 United Kingdom 536401 21328 BALLOONS WRITING SET 1 2010-12-01 1.65 15862 United Kingdom 536

In [0]:
storage_account_name = "sushilstore"
storage_account_key = "BBKRRBiRdx6/0OV+UOSa6nisx4GlnqwwohTVf2YCBBnYKl2Mhbhxi9AnK/hw/ug895yFa2ASSvgs+ASt17JM7Q=="

mount_points = {
    "silver-layer": "/mnt/online-retail/silver-layer",

}

containers = {
    "silver-layer": "silver-layer",
}

def mount_container(container_name, mount_point):
    if not any(mount.mountPoint == mount_point for mount in dbutils.fs.mounts()):
        dbutils.fs.mount(
            source=f"wasbs://{container_name}@{storage_account_name}.blob.core.windows.net",
            mount_point=mount_point,
            extra_configs={f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_key}
        )
        print(f"Mounted {container_name} at {mount_point}")
    else:
        print(f"{mount_point} is already mounted.")

for container, mount_point in mount_points.items():
    mount_container(containers[container], mount_point)

dbutils.fs.mounts()

/mnt/online-retail/silver-layer is already mounted.


[MountInfo(mountPoint='/databricks-datasets', source='databricks-datasets', encryptionType=''),
 MountInfo(mountPoint='/mnt/retail/gold-layer', source='wasbs://gold-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/Volumes', source='UnityCatalogVolumes', encryptionType=''),
 MountInfo(mountPoint='/mnt/online-retail/silver-layer', source='wasbs://silver-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/databricks/mlflow-tracking', source='databricks/mlflow-tracking', encryptionType=''),
 MountInfo(mountPoint='/databricks-results', source='databricks-results', encryptionType=''),
 MountInfo(mountPoint='/databricks/mlflow-registry', source='databricks/mlflow-registry', encryptionType=''),
 MountInfo(mountPoint='/mnt/retail/bronze-layer', source='wasbs://bronze-layer@kushagrahexaware.blob.core.windows.net', encryptionType=''),
 MountInfo(mountPoint='/Volume', source='DbfsReserved', encryptionType=''),
 MountI

In [0]:
Online_Retail_df_cleaned.write.mode("overwrite").parquet("/mnt/online-retail/silver-layer/Online_Retail_df_cleaned")

In [0]:
Online_Retail_df_cleaned_path = "/mnt/online-retail/silver-layer/Online_Retail_df_cleaned"

Online_Retail_df = spark.read.parquet(Online_Retail_df_cleaned_path)

Online_Retail_df.display()

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536367 22310 IVORY KNITTED MUG COSY 6 2010-12-01 1.65 13047 United Kingdom 536388 21523 DOORMAT FANCY FONT HOME SWEET HOME 2 2010-12-01 7.95 16250 United Kingdom 536401 20749 ASSORTED COLOUR MINI CASES 1 2010-12-01 7.95 15862 United Kingdom 536464 22297 HEART IVORY TRELLIS SMALL 1 2010-12-01 1.25 17968 United Kingdom 536500 22712 CARD DOLLY GIRL 12 2010-12-01 0.42 17377 United Kingdom 536576 21354 TOAST ITS - BEST MUM 12 2010-12-01 1.05 13777 United Kingdom 536578 22729 ALARM CLOCK BAKELIKE ORANGE 4 2010-12-01 3.75 17690 United Kingdom 536609 82482 WOODEN PICTURE FRAME WHITE FINISH 6 2010-12-02 2.1 17850 United Kingdom 536615 22467 GUMBALL COAT RACK 12 2010-12-02 2.55 14047 United Kingdom 536617 21356 TOAST ITS - FAIRY FLOWER 12 2010-12-02 1.25 13941 United Kingdom 536638 22210 WOOD STAMP SET BEST WISHES 12 2010-12-02 1.65 16244 United Kingdom 536672 22812 PACK 3 BOXES CHRISTMAS PANNETONE 24 2010-12-02 1.95 14491 United Kingdom C536760 22273 FELTCRAFT DOLL MOLLY 0 2010-12-02 2.95 17547 United Kingdom 536787 21871 SAVE THE PLANET MUG 6 2010-12-02 1.06 17850 United Kingdom 536796 22791 T-LIGHT GLASS FLUTED ANTIQUE 6 2010-12-02 1.25 15574 United Kingdom 536796 22623 BOX OF VINTAGE JIGSAW BLOCKS 1 2010-12-02 4.95 15574 United Kingdom 536798 22426 ENAMEL WASH BOWL CREAM 4 2010-12-02 3.75 17838 United Kingdom 536798 21911 GARDEN METAL SIGN 12 2010-12-02 1.65 17838 United Kingdom 536840 22963 JAM JAR WITH GREEN LID 12 2010-12-02 0.85 12738 Germany 536945 21564 PINK HEART SHAPE LOVE BUCKET 2 2010-12-03 2.95 14083 United Kingdom 536971 22969 HOMEMADE JAM SCENTED CANDLES 12 2010-12-03 1.45 12779 Poland 536974 22659 LUNCH BOX I LOVE LONDON 12 2010-12-03 1.95 12682 France 536975 21179 NO JUNK MAIL METAL SIGN 12 2010-12-03 1.25 14911 EIRE 537030 20969 RED FLORAL FELTCRAFT SHOULDER BAG 8 2010-12-03 3.75 16455 United Kingdom 537034 22633 HAND WARMER UNION JACK 96 2010-12-03 1.85 13081 United Kingdom 537059 22585 PACK OF 6 BIRDY GIFT TAGS 2 2010-12-05 1.25 14813 United Kingdom 537126 84536A ENGLISH ROSE NOTEBOOK A7 SIZE 1 2010-12-05 0.42 18118 United Kingdom 537128 79321 CHILLI LIGHTS 4 2010-12-05 4.95 12841 United Kingdom 537129 84077 WORLD WAR 2 GLIDERS ASSTD DESIGNS 48 2010-12-05 0.29 13506 United Kingdom 537133 22940 FELTCRAFT CHRISTMAS FAIRY 1 2010-12-05 4.25 18156 United Kingdom 537135 20975 12 PENCILS SMALL TUBE RED RETROSPOT 4 2010-12-05 0.65 17059 United Kingdom 537192 21878 PACK OF 6 SANDCASTLE FLAGS ASSORTED 1 2010-12-05 0.85 16402 United Kingdom 537219 22964 3 PIECE SPACEBOY COOKIE CUTTER SET 3 2010-12-05 2.1 14081 United Kingdom 537245 22633 HAND WARMER UNION JACK 12 2010-12-06 2.1 14748 United Kingdom 537255 22374 AIRLINE BAG VINTAGE JET SET RED 4 2010-12-06 4.25 14443 United Kingdom 537332 72760B VINTAGE CREAM 3 BASKET CAKE STAND 2 2010-12-06 9.95 14344 United Kingdom 537350 22556 PLASTERS IN TIN CIRCUS PARADE 12 2010-12-06 1.65 14708 United Kingdom 537366 22569 FELTCRAFT CUSHION BUTTERFLY 10 2010-12-06 3.75 14085 United Kingdom 537369 20751 FUNKY WASHING UP GLOVES ASSORTED 1 2010-12-06 2.1 17860 United Kingdom 537374 22865 HAND WARMER OWL DESIGN 1 2010-12-06 2.1 17259 United Kingdom C537383 21658 GLASS BEURRE DISH 0 2010-12-06 3.95 16550 United Kingdom 537385 22909 SET OF 20 VINTAGE CHRISTMAS NAPKINS 2 2010-12-06 0.85 14487 United Kingdom 537391 22352 LUNCH BOX WITH CUTLERY RETROSPOT 6 2010-12-06 2.55 16550 United Kingdom 537399 22605 WOODEN CROQUET GARDEN SET 3 2010-12-06 14.95 13030 United Kingdom 537400 22099 CARAVAN SQUARE TISSUE BOX 4 2010-12-06 1.25 17191 United Kingdom 537428 21754 HOME BUILDING BLOCK WORD 8 2010-12-06 5.95 17320 United Kingdom 537457 20677 PINK POLKADOT BOWL 72 2010-12-07 1.06 17511 United Kingdom 537465 37370 RETRO COFFEE MUGS ASSORTED 12 2010-12-07 1.25 17735 United Kingdom 537595 84725 FREESTYLE CANVAS ART PICTURE 1 2010-12-07 4.25 13569 United Kingdom 537603 22419 LIPSTICK PEN RED 12 2010-12-07 0.42 14673 United Kingd